In [0]:
from pyspark.sql import functions as F, Window
from pyspark.sql.types import *

In [0]:
# trhs_raw = (spark.read
#     .option("header", "true")       
#     .option("delimiter", ",")         
#     .option("inferSchema", "true")
#     .csv("s3://pprachan-eraneos-data/trhs/*")
# )

# trhs_raw.write.parquet("s3://pprachan-eraneos-data/trhs_parquet")

In [0]:
eurostat_raw = (spark.read.parquet("s3://pprachan-eraneos-data/trhs_parquet"))

citrus_hs6 = ( spark.read
    .option("header", "true")       
    .option("delimiter", ";")              
    .schema(StructType([
        StructField("HS6", StringType(), True),        
        StructField("HS6_NAME", StringType(), True),
        StructField("HS4", StringType(), True),        
        StructField("HS4_NAME", StringType(), True)
    ]))
    .csv("s3://pprachan-eraneos-data/hs6_citrus/")
)

In [0]:
display(eurostat_raw.limit(10))

DECLARANT DECLARANT_ISO PARTNER PARTNER_ISO PRODUCT_HS FLOW TRANSPORT_MODE PERIOD VALUE_IN_EUROS QUANTITY_IN_KG 1 FR 21 XC 160250 2 3 201752 35560 5484 1 FR 21 XC 210690 2 3 201752 1595 111 1 FR 21 XC 220410 2 1 201752 12537 404 1 FR 21 XC 220410 2 3 201752 877 135 1 FR 21 XC 240220 1 4 201752 6685 51 1 FR 21 XC 271019 2 1 201752 14751379 55326199 1 FR 21 XC 271020 2 3 201752 118432 45360 1 FR 21 XC 29SSS5 2 1 201752 408 37 1 FR 21 XC 300212 2 3 201752 6261 95 1 FR 21 XC 300212 2 4 201752 721 18

In [0]:
display(citrus_hs6)


HS6 HS6_NAME HS4 HS4_NAME 080522 Fresh or dried clementines incl. monreales 0805 Citrus fruit, fresh or dried 080529 Fresh or dried wilkings and similar citrus hybrids 0805 Citrus fruit, fresh or dried 080521 Fresh or dried mandarins incl. tangerines and satsumas (excl. clementines) 0805 Citrus fruit, fresh or dried 080520 Fresh or dried mandarins incl. tangerines and satsumas, clementines, wilkings and similar citrus hybrids 0805 Citrus fruit, fresh or dried 080530 Fresh or dried lemons "Citrus limon, Citrus limonum" and limes "Citrus aurantifolia" 0805 Citrus fruit, fresh or dried 080540 Fresh or dried grapefruit 0805 Citrus fruit, fresh or dried 080550 Fresh or dried lemons "Citrus limon, Citrus limonum" and limes "Citrus aurantifolia, Citrus latifolia" 0805 Citrus fruit, fresh or dried 081400 Peel of citrus fruit or melons, incl. watermelons, fresh, frozen, dried or provisionally preserved in brine, or in water with other additives 0814 Peel of citrus fruit or melons, incl. watermelons, fresh, frozen, dried or provisionally preserved in brine, or in water with other additives 080510 Fresh or dried oranges 0805 Citrus fruit, fresh or dried 080590 Fresh or dried citrus fruit (excl. oranges, lemons "Citrus limon, Citrus limonum", limes "Citrus aurantifolia, Citrus latifolia", grapefruit, mandarins, incl. tangerines and satsumas, clementines, wilkings and similar citrus hybrids) 0805 Citrus fruit, fresh or dried

In [0]:
trade_by_hs = eurostat_raw.join(citrus_hs6, eurostat_raw.PRODUCT_HS == citrus_hs6.HS6, "inner")
display(trade_by_hs)

DECLARANT DECLARANT_ISO PARTNER PARTNER_ISO PRODUCT_HS FLOW TRANSPORT_MODE PERIOD VALUE_IN_EUROS QUANTITY_IN_KG HS6 HS6_NAME HS4 HS4_NAME 5 IT 382 ZW 080510 1 1 201752 603602 835943 080510 Fresh or dried oranges 0805 Citrus fruit, fresh or dried 5 IT 388 ZA 080510 1 1 201752 27951446 34619343 080510 Fresh or dried oranges 0805 Citrus fruit, fresh or dried 5 IT 388 ZA 080510 1 3 201752 12800 23680 080510 Fresh or dried oranges 0805 Citrus fruit, fresh or dried 5 IT 388 ZA 080521 1 1 201752 156001 121673 080521 Fresh or dried mandarins incl. tangerines and satsumas (excl. clementines) 0805 Citrus fruit, fresh or dried 5 IT 388 ZA 080522 1 1 201752 160269 129905 080522 Fresh or dried clementines incl. monreales 0805 Citrus fruit, fresh or dried 5 IT 388 ZA 080540 1 1 201752 9474569 8985986 080540 Fresh or dried grapefruit 0805 Citrus fruit, fresh or dried 5 IT 388 ZA 080550 1 1 201752 11157096 9810357 080550 Fresh or dried lemons "Citrus limon, Citrus limonum" and limes "Citrus aurantifolia, Citrus latifolia" 0805 Citrus fruit, fresh or dried 5 IT 388 ZA 080590 1 4 201752 2125 500 080590 Fresh or dried citrus fruit (excl. oranges, lemons "Citrus limon, Citrus limonum", limes "Citrus aurantifolia, Citrus latifolia", grapefruit, mandarins, incl. tangerines and satsumas, clementines, wilkings and similar citrus hybrids) 0805 Citrus fruit, fresh or dried 5 IT 400 US 080510 2 1 201752 149440 114660 080510 Fresh or dried oranges 0805 Citrus fruit, fresh or dried 5 IT 400 US 080550 2 1 201752 108600 74561 080550 Fresh or dried lemons "Citrus limon, Citrus limonum" and limes "Citrus aurantifolia, Citrus latifolia" 0805 Citrus fruit, fresh or dried 5 IT 400 US 080550 2 4 201752 6792 2867 080550 Fresh or dried lemons "Citrus limon, Citrus limonum" and limes "Citrus aurantifolia, Citrus latifolia" 0805 Citrus fruit, fresh or dried 5 IT 400 US 080590 2 4 201752 22760 822 080590 Fresh or dried citrus fruit (excl. oranges, lemons "Citrus limon, Citrus limonum", limes "Citrus aurantifolia, Citrus latifolia", grapefruit, mandarins, incl. tangerines and satsumas, clementines, wilkings and similar citrus hybrids) 0805 Citrus fruit, fresh or dried 5 IT 400 US 081400 2 1 201752 21811 25600 081400 Peel of citrus fruit or melons, incl. watermelons, fresh, frozen, dried or provisionally preserved in brine, or in water with other additives 0814 Peel of citrus fruit or melons, incl. watermelons, fresh, frozen, dried or provisionally preserved in brine, or in water with other additives 5 IT 404 CA 080510 2 1 201752 52271 48024 080510 Fresh or dried oranges 0805 Citrus fruit, fresh or dried 5 IT 404 CA 080550 2 1 201752 16219 9800 080550 Fresh or dried lemons "Citrus limon, Citrus limonum" and limes "Citrus aurantifolia, Citrus latifolia" 0805 Citrus fruit, fresh or dried 5 IT 404 CA 081400 2 1 201752 14420 10000 081400 Peel of citrus fruit or melons, incl. watermelons, fresh, frozen, dried or provisionally preserved in brine, or in water with other additives 0814 Peel of citrus fruit or melons, incl. watermelons, fresh, frozen, dried or provisionally preserved in brine, or in water with other additives 5 IT 412 MX 080540 1 1 201752 116562 125625 080540 Fresh or dried grapefruit 0805 Citrus fruit, fresh or dried 5 IT 412 MX 080550 1 1 201752 1339230 907043 080550 Fresh or dried lemons "Citrus limon, Citrus limonum" and limes "Citrus aurantifolia, Citrus latifolia" 0805 Citrus fruit, fresh or dried 5 IT 412 MX 080550 1 4 201752 193998 89458 080550 Fresh or dried lemons "Citrus limon, Citrus limonum" and limes "Citrus aurantifolia, Citrus latifolia" 0805 Citrus fruit, fresh or dried 5 IT 412 MX 081400 1 1 201752 715483 746092 081400 Peel of citrus fruit or melons, incl. watermelons, fresh, frozen, dried or provisionally preserved in brine, or in water with other additives 0814 Peel of citrus fruit or melons, incl. watermelons, fresh, frozen, dried or provisionally preserved in brine, or in water with other additives 5 IT 452 HT 081400 1 1 201752 25914 8505 0

In [0]:
display(
    trade_by_hs
        .groupBy(F.col("HS4"), F.col("HS4_NAME"))
        .agg(
            F.sum("VALUE_IN_EUROS").alias("total_value"),
            F.sum("QUANTITY_IN_KG").alias("total_quantity")
        )
        .withColumn(
            "pct_value",
            F.col("total_value") / F.sum("total_value").over(Window.partitionBy()) * 100
        )
        .withColumn(
            "pct_quantity",
            F.col("total_quantity") / F.sum("total_quantity").over(Window.partitionBy()) * 100
        )
)


/databricks/python/lib/python3.12/site-packages/pyspark/sql/connect/expressions.py:1134: UserWarning: WARN WindowExpression: No Partition Defined for Window operation! Moving all data to a single partition, this can cause serious performance degradation.
  warnings.warn(


HS4 HS4_NAME total_value total_quantity pct_value pct_quantity 0814 Peel of citrus fruit or melons, incl. watermelons, fresh, frozen, dried or provisionally preserved in brine, or in water with other additives 116966488 73606501 0.8953983592682848 0.4814609429172721 0805 Citrus fruit, fresh or dried 12946100558 15214549700 99.10460164073172 99.51853905708273

0814 representing less than 1% of both the total value and quantity, we decide to focus solely on 0805. 
We update hs6_citrus table to contain only product with the HS code 0805

In [0]:
citrus_hs6_trunc = citrus_hs6.filter(F.col("HS4")=="0805")  
(citrus_hs6_trunc
    .coalesce(1)
    .write.mode("overwrite")
    .option("header", "true")
    .option("delimiter", ";")
    .csv("s3://pprachan-eraneos-data/hs6_citrus_trunc/")
)

# Write parquet files with only 0805 products

In [0]:
display(citrus_hs6_trunc)

HS6 HS6_NAME HS4 HS4_NAME 080522 Fresh or dried clementines incl. monreales 0805 Citrus fruit, fresh or dried 080529 Fresh or dried wilkings and similar citrus hybrids 0805 Citrus fruit, fresh or dried 080521 Fresh or dried mandarins incl. tangerines and satsumas (excl. clementines) 0805 Citrus fruit, fresh or dried 080520 Fresh or dried mandarins incl. tangerines and satsumas, clementines, wilkings and similar citrus hybrids 0805 Citrus fruit, fresh or dried 080530 Fresh or dried lemons "Citrus limon, Citrus limonum" and limes "Citrus aurantifolia" 0805 Citrus fruit, fresh or dried 080540 Fresh or dried grapefruit 0805 Citrus fruit, fresh or dried 080550 Fresh or dried lemons "Citrus limon, Citrus limonum" and limes "Citrus aurantifolia, Citrus latifolia" 0805 Citrus fruit, fresh or dried 080510 Fresh or dried oranges 0805 Citrus fruit, fresh or dried 080590 Fresh or dried citrus fruit (excl. oranges, lemons "Citrus limon, Citrus limonum", limes "Citrus aurantifolia, Citrus latifolia", grapefruit, mandarins, incl. tangerines and satsumas, clementines, wilkings and similar citrus hybrids) 0805 Citrus fruit, fresh or dried

In [0]:
citrus_trade = eurostat_raw.join(citrus_hs6_trunc, eurostat_raw.PRODUCT_HS == citrus_hs6_trunc.HS6, "inner")

In [0]:
citrus_trade.write.parquet("s3://pprachan-eraneos-data/trhs_citrus_parquet")

In [0]:
display(citrus_trade.limit(10))

---------------------------------------------------------------------------
NameError                                 Traceback (most recent call last)
File <command-8768649552423891>, line 1
----> 1 display(citrus_trade.limit(10))

NameError: name 'citrus_trade' is not defined